In [1]:
import os
import os.path as osp
import pandas as pd
import numpy as np
import glob
from tqdm import tqdm

In [2]:
VAL_NPY_DIR = '/data2/yt8m/3/frame/val_npy'
TEST_NPY_DIR = '/data2/yt8m/3/frame/test_npy'
TRAIN_NPY_DIR = '/data2/yt8m/2/frame/train_single_npy'
TRAIN_SIGMOID_NPY_DIR = '/data2/yt8m/2/frame/train_sigmoid_npy_1500'

In [4]:
x = np.load(osp.join(VAL_NPY_DIR, 'JP00.npy'), allow_pickle=True)

In [6]:
x.item()

{'id': 'JP00',
 'labels': [0, 12, 689],
 'segment_labels': [689, 689, 689, 689, 689],
 'segment_end_times': [130, 75, 60, 70, 40],
 'segment_scores': [1.0, 1.0, 1.0, 1.0, 1.0],
 'segment_start_times': [125, 70, 55, 65, 35],
 'rgb_frame': [array([  0,  72, 173, ..., 142, 119, 137], dtype=uint8),
  array([ 34,  44, 156, ..., 124, 218, 146], dtype=uint8),
  array([ 44,  55, 147, ...,  72, 147, 198], dtype=uint8),
  array([ 52,  88, 118, ..., 183, 135,  82], dtype=uint8),
  array([ 31,  75, 120, ..., 169, 117, 119], dtype=uint8),
  array([ 10,  71, 133, ...,  97, 105, 102], dtype=uint8),
  array([  0,  41,  93, ...,  74, 193, 109], dtype=uint8),
  array([192,  50, 124, ..., 103,  73,  15], dtype=uint8),
  array([208,  45, 123, ..., 122,  51,  23], dtype=uint8),
  array([212,  42, 131, ..., 165,  63,  40], dtype=uint8),
  array([208,  43, 129, ...,  99,  43,  10], dtype=uint8),
  array([209,  45, 141, ...,  79,  64,  10], dtype=uint8),
  array([209,  39, 137, ...,  87,  85,  22], dtype=uint

In [8]:
npy_files = glob.glob(VAL_NPY_DIR+'/*.npy')
npy_files[:2]

['/data2/yt8m/3/frame/val_npy/k3pT.npy',
 '/data2/yt8m/3/frame/val_npy/evZC.npy']

In [9]:
len(npy_files)

47087

In [19]:
samples = []
for fn in tqdm(npy_files):
    x = np.load(fn, allow_pickle=True)
    vid = x.item()['id']
    for start_time, end_time, label, score in zip(
        x.item().get('segment_start_times'),
        x.item().get('segment_end_times'),
        x.item().get('segment_labels'),
        x.item().get('segment_scores')):
        samples.append({
            'vid': vid,
            'start_time': start_time,
            'end_time': end_time,
            'label': label,
            'score': score
        })

100%|██████████| 47087/47087 [02:36<00:00, 300.36it/s]


In [20]:
df_val = pd.DataFrame(samples)
df_val = df_val[['vid', 'start_time', 'end_time', 'label', 'score']]
df_val.head()

vid  start_time  end_time  label  score
0  k3pT          35        40     76    1.0
1  k3pT         225       230     76    1.0
2  k3pT         120       125     76    0.0
3  k3pT         165       170     76    1.0
4  k3pT          75        80     76    1.0

In [87]:
0 in df_val.label.unique().tolist()

False

In [21]:
df_val.shape

(237788, 5)

In [22]:
df_val.to_csv('/data2/yt8m/3/frame/val_raw.csv', index=False)

In [40]:
df_val = pd.read_csv('/data2/yt8m/3/frame/val_raw.csv')
df_val.head()

vid  start_time  end_time  label  score
0  k3pT          35        40     76    1.0
1  k3pT         225       230     76    1.0
2  k3pT         120       125     76    0.0
3  k3pT         165       170     76    1.0
4  k3pT          75        80     76    1.0

In [45]:
df_val.label = df_val.apply(lambda x: x.label if x.score==1.0 else 'none', axis=1)
df_val.head()

vid  start_time  end_time label  score
0  k3pT          35        40    76    1.0
1  k3pT         225       230    76    1.0
2  k3pT         120       125  none    0.0
3  k3pT         165       170    76    1.0
4  k3pT          75        80    76    1.0

In [46]:
df_val.to_csv('/data2/yt8m/3/frame/val.csv', index=False)

In [47]:
df_val.dtypes

vid            object
start_time      int64
end_time        int64
label          object
score         float64
dtype: object

In [49]:
len(df_val.label.unique())

1001

In [23]:
df_val.loc[df_val.score==1.0].shape

(132442, 5)

In [35]:
len(df_val.label.unique())

1000

In [30]:
df_class = pd.DataFrame(sorted(df_val.label.unique()), columns=['class'])
df_class.head()

class
0      3
1      7
2      8
3     11
4     12

In [33]:
df_class.to_csv('/data2/yt8m/3/frame/classes.csv', index=False)

# generate test ids

In [51]:
test_npy_files = glob.glob(TEST_NPY_DIR+'/*.npy')
len(test_npy_files)

44753

In [52]:
test_npy_files[:2]

['/data2/yt8m/3/frame/test_npy/MeVj.npy',
 '/data2/yt8m/3/frame/test_npy/nBeX.npy']

In [54]:
x = np.load(osp.join(TEST_NPY_DIR, 'MeVj.npy'), allow_pickle=True)
x.item()

{'id': 'MeVj',
 'rgb_frame': [array([  0,  72, 173, ..., 142, 119, 137], dtype=uint8),
  array([ 84, 185,  74, ..., 141, 129, 137], dtype=uint8),
  array([ 53, 201, 102, ..., 135, 246, 162], dtype=uint8),
  array([195, 162, 102, ..., 228,  76, 106], dtype=uint8),
  array([114, 117,  86, ..., 143, 103,  92], dtype=uint8),
  array([111, 130,  56, ...,  60, 122,  13], dtype=uint8),
  array([193, 116, 103, ..., 135, 112, 216], dtype=uint8),
  array([233,  56,  83, ..., 153,  36,  93], dtype=uint8),
  array([237,  56,  74, ..., 116,  29,  82], dtype=uint8),
  array([220,  67,  62, ..., 163, 156, 131], dtype=uint8),
  array([206,  41,  66, ..., 168,  68, 111], dtype=uint8),
  array([211,  55,  74, ...,  79,   5, 138], dtype=uint8),
  array([255,  43,  92, ..., 198,  76, 139], dtype=uint8),
  array([229,  47,  73, ..., 138,  98,  59], dtype=uint8),
  array([227,  50,  78, ..., 121,  41, 110], dtype=uint8),
  array([231,  58,  84, ...,  90,   1, 114], dtype=uint8),
  array([189,  53,  63, ...,

In [57]:
len(x.item()['rgb_frame'])

300

In [69]:
samples = []
for fn in tqdm(test_npy_files):
    x = np.load(fn, allow_pickle=True)
    vid = x.item()['id']
    n_frames = len(x.item()['rgb_frame'])
    for i in range(n_frames//5):
        samples.append({
            'vid': vid,
            'start_time': i*5
        })


100%|██████████| 44753/44753 [02:25<00:00, 308.45it/s]


In [71]:
df_test = pd.DataFrame(samples)
df_test = df_test[['vid', 'start_time']]
df_test.head()

vid  start_time
0  MeVj           0
1  MeVj           5
2  MeVj          10
3  MeVj          15
4  MeVj          20

In [75]:
def get_seg_id(row):
    return '{}:{}'.format(row.vid, row.start_time)

In [76]:
df_test['seg_id'] = df_test.apply(lambda x: get_seg_id(x), axis=1)

In [77]:
df_test.head()

vid  start_time   seg_id
0  MeVj           0   MeVj:0
1  MeVj           5   MeVj:5
2  MeVj          10  MeVj:10
3  MeVj          15  MeVj:15
4  MeVj          20  MeVj:20

In [78]:
df_test.shape

(2038114, 3)

In [79]:
df_test.to_csv('/data2/yt8m/3/frame/test_ids.csv', index=False)

In [68]:
for i in range(21//5):
    print(i*5)

0
5
10
15


# convert frame level training data

In [94]:
train_npy_files = glob.glob(TRAIN_NPY_DIR+'/*.npy')
train_npy_files[:2]

['/data2/yt8m/2/frame/train_single_npy/SldJ.npy',
 '/data2/yt8m/2/frame/train_single_npy/O12T.npy']

In [95]:
len(train_npy_files)

370869

In [91]:
x = np.load(osp.join(TRAIN_NPY_DIR, 'SldJ.npy'), allow_pickle=True)

In [92]:
x.item()

{'id': 'SldJ',
 'labels': [52],
 'rgb_frame': [array([  0,  73, 161, ...,  98, 117, 132], dtype=uint8),
  array([ 92, 144,  40, ...,  66, 116,  80], dtype=uint8),
  array([ 93, 125,  40, ...,  74,   0, 126], dtype=uint8),
  array([ 97, 113,  47, ...,  67,  16,  78], dtype=uint8),
  array([ 94, 121,  46, ...,  40,  28, 126], dtype=uint8),
  array([141,  99,  65, ...,  83,  48,  84], dtype=uint8),
  array([127, 147,  46, ..., 198, 184,  98], dtype=uint8),
  array([127, 146,  46, ..., 190, 185, 100], dtype=uint8),
  array([159, 209, 102, ..., 223, 159, 127], dtype=uint8),
  array([153, 215, 112, ..., 107, 204,  43], dtype=uint8),
  array([140, 197,  96, ..., 128, 140, 156], dtype=uint8),
  array([120, 200,  99, ..., 108, 175, 153], dtype=uint8),
  array([169, 202,  98, ...,  74,   0, 212], dtype=uint8),
  array([110, 188, 110, ..., 186, 106,  47], dtype=uint8),
  array([ 40, 225, 124, ..., 196, 100,  80], dtype=uint8),
  array([123, 228, 115, ...,  84,   4, 194], dtype=uint8),
  array([ 4

In [93]:
len(x.item()['rgb_frame'])

179

In [97]:
samples = []
for fn in tqdm(train_npy_files):
    x = np.load(fn, allow_pickle=True)
    vid = x.item()['id']
    label = x.item()['labels'][0]
    samples.append({
        'vid': vid,
        'label': label,
        'nframes': len(x.item()['rgb_frame'])
    })


  0%|          | 1740/370869 [00:32<2:08:44, 47.79it/s]


  1%|          | 3439/370869 [01:03<1:50:47, 55.27it/s]


  1%|▏         | 5153/370869 [01:34<1:46:43, 57.11it/s]


  2%|▏         | 6869/370869 [02:06<1:48:25, 55.96it/s]


  2%|▏         | 8575/370869 [02:38<1:48:15, 55.77it/s]


...

 98%|█████████▊| 364494/370869 [1:56:05<02:01, 52.32it/s]


 99%|█████████▊| 366136/370869 [1:56:36<01:29, 52.79it/s]


 99%|█████████▉| 367803/370869 [1:57:07<00:52, 58.86it/s]


100%|█████████▉| 369467/370869 [1:57:38<00:25, 54.51it/s]


100%|██████████| 370869/370869 [1:58:04<00:00, 52.35it/s]

In [98]:
df_train = pd.DataFrame(samples)
df_train = df_train[['vid', 'label', 'nframes']]
df_train.head()

vid  label  nframes
0  SldJ     52      179
1  O12T    194      207
2  reyF      8      218
3  wbQD      8      300
4  StY6     31      284

In [99]:
df_train.to_csv('/data2/yt8m/3/frame/train_single_1000.csv', index=False)

In [103]:
df_train.nframes.value_counts()

300    102712
180      2322
120      2185
121      1927
125      1855
122      1815
131      1814
123      1798
126      1794
132      1785
150      1764
124      1762
128      1754
210      1743
240      1740
192      1735
181      1730
134      1725
130      1724
135      1719
182      1714
190      1711
137      1710
200      1709
178      1707
183      1707
188      1698
195      1697
189      1696
186      1695
        ...  
109         2
55          2
69          2
27          2
58          2
111         1
12          1
113         1
7           1
106         1
9           1
105         1
100         1
96          1
45          1
95          1
13          1
90          1
30          1
79          1
75          1
73          1
72          1
63          1
62          1
23          1
61          1
48          1
32          1
67          1
Name: nframes, Length: 225, dtype: int64

# sigmoid train data

In [7]:
x = np.load(osp.join(TRAIN_SIGMOID_NPY_DIR, '000k.npy'), allow_pickle=True)

In [8]:
x.item()

{'id': '000k',
 'labels': [17, 129, 19],
 'rgb_frame': [array([117,  16,  50, ..., 159, 163, 177], dtype=uint8),
  array([146,  49,  42, ..., 173, 211, 207], dtype=uint8),
  array([120,  73,  79, ..., 186, 238, 255], dtype=uint8),
  array([ 83, 146,  86, ...,  36, 217,  54], dtype=uint8),
  array([122,  82,  44, ..., 148,  94, 170], dtype=uint8),
  array([ 98, 116,  60, ..., 146,  87, 130], dtype=uint8),
  array([140, 102,  61, ..., 209, 158, 112], dtype=uint8),
  array([ 62, 167,  86, ..., 151, 176, 255], dtype=uint8),
  array([ 63, 136,  91, ..., 190, 170, 216], dtype=uint8),
  array([ 55, 164,  83, ..., 200, 162, 249], dtype=uint8),
  array([ 85, 137,  87, ..., 194,  80, 154], dtype=uint8),
  array([ 77, 121,  59, ..., 128,  75,  92], dtype=uint8),
  array([115, 135,  77, ..., 130,  26, 152], dtype=uint8),
  array([147, 120,  75, ..., 184,  89, 124], dtype=uint8),
  array([127,  85,  89, ..., 236, 186,  95], dtype=uint8),
  array([ 86, 138,  79, ..., 255, 114, 232], dtype=uint8),
  

In [9]:
type(x.item()['labels'][0])

int

In [3]:
train_simoid_npy_files = glob.glob(TRAIN_SIGMOID_NPY_DIR+'/*.npy')
train_simoid_npy_files[:2]

['/data2/yt8m/2/frame/train_sigmoid_npy_1500/SldJ.npy',
 '/data2/yt8m/2/frame/train_sigmoid_npy_1500/O12T.npy']

In [4]:
len(train_simoid_npy_files)

1010343

In [5]:
samples = []
for fn in tqdm(train_simoid_npy_files):
    x = np.load(fn, allow_pickle=True)
    vid = x.item()['id']
    label = x.item()['labels']
    samples.append({
        'vid': vid,
        'label': label,
        'nframes': len(x.item()['rgb_frame'])
    })

100%|██████████| 1010343/1010343 [5:20:45<00:00, 52.50it/s]  


In [6]:
df_train = pd.DataFrame(samples)
df_train = df_train[['vid', 'label', 'nframes']]
df_train.head()

vid       label  nframes
0  SldJ        [52]      179
1  O12T       [194]      207
2  SYwy  [121, 207]      300
3  reyF         [8]      218
4  rIiw    [33, 28]      184

In [7]:
df_train.to_csv('/data2/yt8m/3/frame/train_sigmoid_1500.csv', index=False)

In [8]:
df = pd.read_csv('/data2/yt8m/3/frame/train_sigmoid_1500.csv', converters={'label': eval})
df.head()

vid       label  nframes
0  SldJ        [52]      179
1  O12T       [194]      207
2  SYwy  [121, 207]      300
3  reyF         [8]      218
4  rIiw    [33, 28]      184

In [9]:
df.iloc[2].label[1]

207